In [1]:
import logging
import os

import pypsa
import yaml
import pandas as pd
import geopandas as gpd
import geoviews as gv
import hvplot.pandas
import numpy as np
import scipy as sp
import networkx as nx
import matplotlib as plt

from scipy.sparse import csgraph
from itertools import product

from shapely.geometry import Point, LineString
import shapely, shapely.prepared, shapely.wkt

logger = logging.getLogger(__name__)

pd.set_option("display.max_columns", None)
pd.set_option("display.max_colwidth", 70)

import sys

sys.path.append("../")  # to import helpers
from scripts._helpers import sets_path_to_root

sets_path_to_root("pypsa-africa")

This is the repository path:  c:\Users\Davide\Git\pypsa-africa
Had to go 1 folder(s) up.


In [2]:
network_path = os.getcwd() + "/networks/elec.nc"
n = pypsa.Network(network_path)
n

INFO:pypsa.io:Imported network elec_s.nc has buses, carriers, generators, lines, loads


Network PyPSA-Eur

In [3]:
n.buses

v_nom  tag_substation  tag_area       lon        lat country         x  \
name                                                                           
0     380.0           False     False  4.820742   9.168124      NG  4.820742   
1     380.0           False     False  7.410959  10.591259      NG  7.410959   
2     380.0           False     False  7.478004   9.114552      NG  7.478004   
3     380.0           False     False  8.569306   7.627241      NG  8.569306   
4     380.0           False     False  3.533724   6.774068      NG  3.533724   
...     ...             ...       ...       ...        ...     ...       ...   
895   380.0           False     False  5.460619  10.379371      NG  5.460619   
896   380.0           False     False  4.820841   9.167156      NG  4.820841   
897   380.0           False     False  8.474327  11.927053      NG  8.474327   
898   380.0           False     False  7.538300   6.457656      NG  7.538300   
899   380.0           False     False  4.155314   7.628119      NG  4.155314   

              y type carrier  unit  v_mag_pu_set  v_mag_pu_min  v_mag_pu_max  \
name                                                                           
0      9.168124           AC  None           1.0           0.0           inf   
1     10.591259           AC  None           1.0           0.0           inf   
2      9.114552           AC  None           1.0           0.0           inf   
3      7.627241           AC  None           1.0           0.0           inf   
4      6.774068           AC  None           1.0           0.0           inf   
...         ...  ...     ...   ...           ...           ...           ...   
895   10.379371           AC  None           1.0           0.0           inf   
896    9.167156           AC  None           1.0           0.0           inf   
897   11.927053           AC  None           1.0           0.0           inf   
898    6.457656           AC  None           1.0           0.0           inf   
899    7.628119           AC  None           1.0           0.0           inf   

     control sub_network  
name                      
0         PQ              
1         PQ              
2         PQ              
3         PQ              
4         PQ              
...      ...         ...  
895       PQ              
896       PQ              
897       PQ              
898       PQ              
899       PQ              

[900 rows x 16 columns]

In [4]:
n.lines

bus0 bus1  v_nom  num_parallel      length  underground  \
name                                                                  
574136280-1    0  450  380.0      0.623269    0.044676        False   
266473495-1    1  451  380.0      0.623269  100.938650        False   
565862689-1    2  452  380.0      0.335180    1.866475        False   
782531821-1    3  453  380.0      0.623269    0.112987        False   
534403748-1    4  454  380.0      1.246537  128.923270        False   
...          ...  ...    ...           ...         ...          ...   
566807641-1  445  895  380.0      0.335180   97.801920        False   
477596991-1  446  896  380.0      0.623269  159.954955        False   
266549273-1  447  897  380.0      0.623269  206.828684        False   
575666912-1  448  898  380.0      0.335180    0.015046        False   
696198028-1  449  899  380.0      0.335180   24.694164        False   

             under_construction tag_type  tag_frequency country  \
name                                                              
574136280-1               False     line             50      NG   
266473495-1               False     line             50      NG   
565862689-1               False     line             50      NG   
782531821-1               False     line             50      NG   
534403748-1               False     line             50      NG   
...                         ...      ...            ...     ...   
566807641-1               False     line             50      NG   
477596991-1               False     line             50      NG   
266549273-1               False     line             50      NG   
575666912-1               False     line             50      NG   
696198028-1               False     line             50      NG   

                                                                          geometry  \
name                                                                                 
574136280-1  LINESTRING (4.8207423 9.168124000000001, 4.820657700000011 9.1685113)   
266473495-1  LINESTRING (7.4109595 10.59125850000006, 7.410532 10.5913801000000...   
565862689-1  LINESTRING (7.4780041 9.114552099999999, 7.4787846 9.1147348000000...   
782531821-1  LINESTRING (8.569306100000045 7.627240599999407, 8.568782100000023...   
534403748-1  LINESTRING (3.5337245 6.774067800000018, 3.537493 6.77387070000001...   
...                                                                            ...   
566807641-1  LINESTRING (4.753426899999983 10.81075719999999, 4.754443499999984...   
477596991-1  LINESTRING (4.578024699999951 7.802427500000015, 4.579957899999951...   
266549273-1  LINESTRING (7.411249 10.59214940000006, 7.41059940000004 10.592411...   
575666912-1           LINESTRING (7.538166 6.457671600000013, 7.5383002 6.4576556)   
696198028-1  LINESTRING (4.038540200000029 7.452455800000013, 4.039491300000029...   

                                                                            bounds  \
name                                                                                 
574136280-1  MULTIPOINT (4.8207423 9.168124000000001, 4.820657700000011 9.1685113)   
266473495-1  MULTIPOINT (7.4109595 10.59125850000006, 6.8296632 9.972979600000022)   
565862689-1          MULTIPOINT (7.4780041 9.114552099999999, 7.4945265 9.1132147)   
782531821-1  MULTIPOINT (8.569306100000045 7.627240599999407, 8.568362300000024...   
534403748-1  MULTIPOINT (3.5337245 6.774067800000018, 4.6538365 6.720406300000104)   
...                                                                            ...   
566807641-1  MULTIPOINT (4.753426899999983 10.81075719999999, 5.460619499999982...   
477596991-1  MULTIPOINT (4.578024699999951 7.802427500000015, 4.820841400000011...   
266549273-1  MULTIPOINT (7.411249 10.59214940000006, 8.474326700000001 11.92705...   
575666912-1           MULTIPOINT (7.538166 6.457671600000013, 7.5383002 6.4576556)   
696198028-1  MULTIPOINT (4.038540200000029 7.452455800000013, 4.1

In [5]:
# Try to make the points 'right'
# TODO: issue at n.plot in plot.py of PyPSA

# df = n.buses
# df["geometry"] = gpd.points_from_xy(df.lon, df.lat)
# gdf = gpd.GeoDataFrame(df, crs='epsg:4326')
# n.buses = gdf


# #import geoplot
# import matplotlib.pyplot as plt
# import cartopy.crs as ccrs

# #Germany shape information
# world = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))
# africa = world.query('continent == "Africa"')

# #Boundary coordinates for Germany
# xlim = ([africa.total_bounds[0],  africa.total_bounds[2]])
# ylim = ([africa.total_bounds[1],  africa.total_bounds[3]])

# #plot
# fig,ax = plt.subplots(1,1,subplot_kw={"projection":ccrs.PlateCarree()})
# fig.set_size_inches(15,15)
# ax = n.plot(ax=ax, boundaries = xlim+ylim, bus_sizes=1, geometry = True)

In [6]:
from shapely import wkt

lines = n.lines
lines["geometry"] = lines["geometry"].apply(wkt.loads)
lines = gpd.GeoDataFrame(lines, crs="epsg:4326")

buses = n.buses
buses["geometry"] = gpd.points_from_xy(buses.lon, buses.lat)
buses = gpd.GeoDataFrame(buses, crs="epsg:4326")

C:\ProgramData\Miniconda3\envs\toast\lib\site-packages\geopandas\array.py:275: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  return GeometryArray(vectorized.points_from_xy(x, y, z), crs=crs)


In [7]:
lines

bus0 bus1  v_nom  num_parallel      length  underground  \
name                                                                  
574136280-1    0  450  380.0      0.623269    0.044676        False   
266473495-1    1  451  380.0      0.623269  100.938650        False   
565862689-1    2  452  380.0      0.335180    1.866475        False   
782531821-1    3  453  380.0      0.623269    0.112987        False   
534403748-1    4  454  380.0      1.246537  128.923270        False   
...          ...  ...    ...           ...         ...          ...   
566807641-1  445  895  380.0      0.335180   97.801920        False   
477596991-1  446  896  380.0      0.623269  159.954955        False   
266549273-1  447  897  380.0      0.623269  206.828684        False   
575666912-1  448  898  380.0      0.335180    0.015046        False   
696198028-1  449  899  380.0      0.335180   24.694164        False   

             under_construction tag_type  tag_frequency country  \
name                                                              
574136280-1               False     line             50      NG   
266473495-1               False     line             50      NG   
565862689-1               False     line             50      NG   
782531821-1               False     line             50      NG   
534403748-1               False     line             50      NG   
...                         ...      ...            ...     ...   
566807641-1               False     line             50      NG   
477596991-1               False     line             50      NG   
266549273-1               False     line             50      NG   
575666912-1               False     line             50      NG   
696198028-1               False     line             50      NG   

                                                                          geometry  \
name                                                                                 
574136280-1                          LINESTRING (4.82074 9.16812, 4.82066 9.16851)   
266473495-1  LINESTRING (7.41096 10.59126, 7.41053 10.59138, 7.40724 10.58993, ...   
565862689-1  LINESTRING (7.47800 9.11455, 7.47878 9.11473, 7.48053 9.11523, 7.4...   
782531821-1         LINESTRING (8.56931 7.62724, 8.56878 7.62696, 8.56836 7.62695)   
534403748-1  LINESTRING (3.53372 6.77407, 3.53749 6.77387, 3.55693 6.77303, 3.5...   
...                                                                            ...   
566807641-1  LINESTRING (4.75343 10.81076, 4.75444 10.80972, 4.75591 10.80824, ...   
477596991-1  LINESTRING (4.57802 7.80243, 4.57996 7.80521, 4.57917 7.80741, 4.5...   
266549273-1  LINESTRING (7.41125 10.59215, 7.41060 10.59241, 7.40899 10.59499, ...   
575666912-1                          LINESTRING (7.53817 6.45767, 7.53830 6.45766)   
696198028-1  LINESTRING (4.03854 7.45246, 4.03949 7.45275, 4.04077 7.45401, 4.0...   

                                                                            bounds  \
name                                                                                 
574136280-1  MULTIPOINT (4.8207423 9.168124000000001, 4.820657700000011 9.1685113)   
266473495-1  MULTIPOINT (7.4109595 10.59125850000006, 6.8296632 9.972979600000022)   
565862689-1          MULTIPOINT (7.4780041 9.114552099999999, 7.4945265 9.1132147)   
782531821-1  MULTIPOINT (8.569306100000045 7.627240599999407, 8.568362300000024...   
534403748-1  MULTIPOINT (3.5337245 6.774067800000018, 4.6538365 6.720406300000104)   
...                                                                            ...   
566807641-1  MULTIPOINT (4.753426899999983 10.81075719999999, 5.460619499999982...   
477596991-1  MULTIPOINT (4.578024699999951 7.802427500000015, 4.820841400000011...   
266549273-1  MULTIPOINT (7.411249 10.59214940000006, 8.474326700000001 11.92705...   
575666912-1           MULTIPOINT (7.538166 6.457671600000013, 7.5383002 6.4576556)   
696198028-1  MULTIPOINT (4.038540200000029 7.452455800000013, 4.1

In [8]:
buses

v_nom  tag_substation  tag_area       lon        lat country         x  \
name                                                                           
0     380.0           False     False  4.820742   9.168124      NG  4.820742   
1     380.0           False     False  7.410959  10.591259      NG  7.410959   
2     380.0           False     False  7.478004   9.114552      NG  7.478004   
3     380.0           False     False  8.569306   7.627241      NG  8.569306   
4     380.0           False     False  3.533724   6.774068      NG  3.533724   
...     ...             ...       ...       ...        ...     ...       ...   
895   380.0           False     False  5.460619  10.379371      NG  5.460619   
896   380.0           False     False  4.820841   9.167156      NG  4.820841   
897   380.0           False     False  8.474327  11.927053      NG  8.474327   
898   380.0           False     False  7.538300   6.457656      NG  7.538300   
899   380.0           False     False  4.155314   7.628119      NG  4.155314   

              y type carrier  unit  v_mag_pu_set  v_mag_pu_min  v_mag_pu_max  \
name                                                                           
0      9.168124           AC  None           1.0           0.0           inf   
1     10.591259           AC  None           1.0           0.0           inf   
2      9.114552           AC  None           1.0           0.0           inf   
3      7.627241           AC  None           1.0           0.0           inf   
4      6.774068           AC  None           1.0           0.0           inf   
...         ...  ...     ...   ...           ...           ...           ...   
895   10.379371           AC  None           1.0           0.0           inf   
896    9.167156           AC  None           1.0           0.0           inf   
897   11.927053           AC  None           1.0           0.0           inf   
898    6.457656           AC  None           1.0           0.0           inf   
899    7.628119           AC  None           1.0           0.0           inf   

     control sub_network                  geometry  
name                                                
0         PQ               POINT (4.82074 9.16812)  
1         PQ              POINT (7.41096 10.59126)  
2         PQ               POINT (7.47800 9.11455)  
3         PQ               POINT (8.56931 7.62724)  
4         PQ               POINT (3.53372 6.77407)  
...      ...         ...                       ...  
895       PQ              POINT (5.46062 10.37937)  
896       PQ               POINT (4.82084 9.16716)  
897       PQ              POINT (8.47433 11.92705)  
898       PQ               POINT (7.53830 6.45766)  
899       PQ               POINT (4.15531 7.62812)  

[900 rows x 17 columns]

In [9]:
# lines = lines[lines["country"]=="nigeria"]
# buses = buses[buses["country"]=="nigeria"]

buses.hvplot(
    geo=True,
    size=10,  # buses["tag_area"]**(0.5)/10,
    frame_height=750,
    alpha=0.4,
    tiles="CartoLight",
    hover_cols=["bus_id"],
    color="orange",
) * lines.hvplot(geo=True, alpha=0.4, hover_cols=["line_id"]).opts(
    active_tools=["pan", "wheel_zoom"]
)

C:\ProgramData\Miniconda3\envs\toast\lib\site-packages\cartopy\crs.py:228: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  if len(multi_line_string) > 1:
C:\ProgramData\Miniconda3\envs\toast\lib\site-packages\cartopy\crs.py:280: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for line in multi_line_string:
C:\ProgramData\Miniconda3\envs\toast\lib\site-packages\cartopy\crs.py:347: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  if len(p_mline) > 0:
C:\ProgramData\Miniconda3\envs\toast\lib\site-packages\cartop

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Longitude,Latitude]
   .Path.I   :Path   [Longitude,Latitude]

In [10]:
buses

v_nom  tag_substation  tag_area       lon        lat country         x  \
name                                                                           
0     380.0           False     False  4.820742   9.168124      NG  4.820742   
1     380.0           False     False  7.410959  10.591259      NG  7.410959   
2     380.0           False     False  7.478004   9.114552      NG  7.478004   
3     380.0           False     False  8.569306   7.627241      NG  8.569306   
4     380.0           False     False  3.533724   6.774068      NG  3.533724   
...     ...             ...       ...       ...        ...     ...       ...   
895   380.0           False     False  5.460619  10.379371      NG  5.460619   
896   380.0           False     False  4.820841   9.167156      NG  4.820841   
897   380.0           False     False  8.474327  11.927053      NG  8.474327   
898   380.0           False     False  7.538300   6.457656      NG  7.538300   
899   380.0           False     False  4.155314   7.628119      NG  4.155314   

              y type carrier  unit  v_mag_pu_set  v_mag_pu_min  v_mag_pu_max  \
name                                                                           
0      9.168124           AC  None           1.0           0.0           inf   
1     10.591259           AC  None           1.0           0.0           inf   
2      9.114552           AC  None           1.0           0.0           inf   
3      7.627241           AC  None           1.0           0.0           inf   
4      6.774068           AC  None           1.0           0.0           inf   
...         ...  ...     ...   ...           ...           ...           ...   
895   10.379371           AC  None           1.0           0.0           inf   
896    9.167156           AC  None           1.0           0.0           inf   
897   11.927053           AC  None           1.0           0.0           inf   
898    6.457656           AC  None           1.0           0.0           inf   
899    7.628119           AC  None           1.0           0.0           inf   

     control sub_network                  geometry  
name                                                
0         PQ               POINT (4.82074 9.16812)  
1         PQ              POINT (7.41096 10.59126)  
2         PQ               POINT (7.47800 9.11455)  
3         PQ               POINT (8.56931 7.62724)  
4         PQ               POINT (3.53372 6.77407)  
...      ...         ...                       ...  
895       PQ              POINT (5.46062 10.37937)  
896       PQ               POINT (4.82084 9.16716)  
897       PQ              POINT (8.47433 11.92705)  
898       PQ               POINT (7.53830 6.45766)  
899       PQ               POINT (4.15531 7.62812)  

[900 rows x 17 columns]

# TEST AREA - to test single functions

In [11]:
lines = (
    pd.read_csv(
        "data/osm/africa_all_lines_build_network.csv",
        dtype=dict(
            line_id="str",
            bus0="str",
            bus1="str",
            underground="bool",
            under_construction="bool",
        ),
    )
    .set_index("line_id")
    .rename(columns=dict(voltage="v_nom", circuits="num_parallel"))
)

lines["length"] /= 1e3  # m to km conversion
lines["v_nom"] /= 1e3  # V to kV conversion
lines = lines.loc[:, ~lines.columns.str.contains("^Unnamed")]
lines = _rebase_voltage_to_config(lines)

# lines

FileNotFoundError: [Errno 2] No such file or directory: 'data/osm/africa_all_lines_build_network.csv'

In [ ]:
def _rebase_voltage_to_config(component):
    """
    Rebase the voltage of components to the config.yaml input

    Components such as line and buses have voltage levels between
    110 kV up to around 850 kV. PyPSA-Africa uses 3 voltages as config input.
    This function rebases all inputs to the lower, middle and upper voltage
    bound.

    Parameters
    ----------
    component : dataframe
    """
    v_min = 110  # min. filtered value in dataset
    v_low = 110
    v_mid = 220
    v_up = 330
    v_low_mid = (v_mid - v_low) / 2 + v_low  # between low and mid voltage
    v_mid_up = (v_up - v_mid) / 2 + v_mid  # between mid and upper voltage
    component.loc[
        (v_min <= component["v_nom"]) & (component["v_nom"] < v_low_mid), "v_nom"
    ] = v_low
    component.loc[
        (v_low_mid <= component["v_nom"]) & (component["v_nom"] < v_mid_up), "v_nom"
    ] = v_mid
    component.loc[v_mid_up <= component["v_nom"], "v_nom"] = v_up

    return component